# df is for NBI time series data and df_NOAA is for the datset containing NOAA features

In [1]:
from pandas import read_csv

df = read_csv('Time_Series_For_Clustering_El_Paso_Final.csv')
df_NOAA = read_csv('NBI_NOAA_Integrated.csv')

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\IPython\core\interactiveshell.py:3147: DtypeWarning: Columns (19,33,38,39,40,41,43,71,78,81,104,108,109,110,111,116,132,135) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


# get each separate time series as an individual list and append each of these lists to a master list

In [2]:
import re
import pandas as pd

non_decimal = re.compile(r'[^\d.]+')

list_of_training_df = []
list_of_row_components = []

for i in range(1, 524):
    
    current_row = df.iloc[i]
    
    bridge_id = current_row.iloc[0]
    
    current_row = current_row.iloc[1:]
    
    for j, row in current_row.iteritems():
        
        current_row_components = row.split(', ')
        current_row_components_replaced = []
        
        current_row_components_replaced.append(bridge_id)

        for idx, component in enumerate(current_row_components):

            result = non_decimal.sub('', current_row_components[idx])
            current_row_components_replaced.append(float(result))

        list_of_row_components.append(current_row_components_replaced)

# Ensure each element in the list of lists is a float

In [3]:
for idx, element in enumerate(list_of_row_components):
    for i in range(1, len(element)):
        list_of_row_components[idx][i] = float(list_of_row_components[idx][i])

# View one time series

In [4]:
for i in range(22): # 0 to 21
    print(list_of_row_components[i])

['CALHAN-8TH ST. ', 36.0, 97.0, 428.0, 1949.0, 2.0, 10.9, 7.3]
['CALHAN-8TH ST. ', 36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3]
['CALHAN-8TH ST. ', 36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3]
['CALHAN-8TH ST. ', 36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3]
['CALHAN-8TH ST. ', 36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 955.0, 1949.0, 2.0, 11.0, 7.0]
['CALHAN-8TH ST. ', 36.3, 96.9, 955.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 96.9, 983.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 96.9, 983.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 96.9, 983.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 96.9, 983.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 422.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 422.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 422.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 422.0, 1949.0, 2.0, 11.0, 7.3]
['CALHAN-8TH ST. ', 36.3, 97.0, 422.0, 1949.0, 2.0, 9.7

# Get length of list of lists

In [6]:
len(list_of_row_components)

11506

# Swap last entry with second entry in time series to make the output predictor variable Sufficiency Rating

In [7]:
# for idx, component in enumerate(list_of_row_components):
#     temp = component[6]
#     list_of_row_components[idx][6] = list_of_row_components[idx][1]
#     list_of_row_components[idx][1] = temp

# Convert format of list to have a single time series for each index

In [8]:
import numpy as np

list_of_examples = []
temp_list = []

max_num = 22
iter = 0;

for row_component in list_of_row_components:
    if iter == max_num:
        list_of_examples.append(np.array(temp_list))
        temp_list = []
        iter = 0
        
    temp_list.append(np.array(row_component))
    iter += 1

list_of_examples = np.array(list_of_examples)

# Concatenate corresponding features from the NOAA data to each of the time series steps

In [9]:
start_year = 1998
last_year = 2019

rows = []

for i, example in enumerate(list_of_row_components):
        
        row = df_NOAA.loc[(df_NOAA['STRUCTURE_NUMBER_008'] == list_of_row_components[i][0]) & (df_NOAA['EVALUATION_YEAR'] == start_year)]
        
        for idx, r in row.iterrows():  
            list_of_row_components[i].append(r['prcp_avg'])
            list_of_row_components[i].append(r['snow_avg'])
            list_of_row_components[i].append(r['snwd_avg'])
        
        if len(row) == 0:
            row = prev_row
            
        start_year += 1
        
        if start_year > last_year:
            start_year = 1998
            
        prev_row = row
        prev_row['EVALUATION_YEAR'] = start_year
        

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

...

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\tobby\Anaconda3\envs\tf_bridge_management\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value

# View single time series step with newly added weather data

In [10]:
list_of_row_components[0]

['CALHAN-8TH ST. ',
 36.0,
 97.0,
 428.0,
 1949.0,
 2.0,
 10.9,
 7.3,
 0.06572289156626507,
 0.3060240963855422,
 1.5301204819277108]

# Create a list of dictionaries where each dictionary contains a single time series along with a bridge id to identify which bridge it is

In [14]:
max_chunk = 22
counter = 0

temp_dict = {}
list_of_dicts = []

for i in range(11506):
    
    if counter == max_chunk:
        list_of_dicts.append(temp_dict)
        temp_dict = {}
        counter = 0
    
    if counter == 0:
        if 'Bridge_id' not in temp_dict:
            temp_dict['Bridge_id'] = list_of_row_components[i][0]
            
    if 'time_{}'.format(counter) not in temp_dict:
        temp_dict['time_{}'.format(counter)] = list_of_row_components[i][1:]
        
    counter += 1

# View one dictionary from this list

In [15]:
list_of_dicts[0]

{'Bridge_id': 'CALHAN-8TH ST. ',
 'time_0': [36.0,
  97.0,
  428.0,
  1949.0,
  2.0,
  10.9,
  7.3,
  0.06572289156626507,
  0.3060240963855422,
  1.5301204819277108],
 'time_1': [36.0,
  96.9,
  955.0,
  1949.0,
  2.0,
  10.9,
  7.3,
  0.08709589041095896,
  0.31643835616438354,
  0.7397260273972602],
 'time_2': [36.0,
  96.9,
  955.0,
  1949.0,
  2.0,
  10.9,
  7.3,
  0.052734806629834256,
  0.2842541436464089,
  0.7983425414364641],
 'time_3': [36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3],
 'time_4': [36.0,
  96.9,
  955.0,
  1949.0,
  2.0,
  10.9,
  7.3,
  0.01994505494505494,
  0.04697802197802199,
  0.046703296703296704],
 'time_5': [36.3,
  97.0,
  955.0,
  1949.0,
  2.0,
  11.0,
  7.0,
  0.06424489795918364,
  0.015918367346938776,
  0.0],
 'time_6': [36.3,
  96.9,
  955.0,
  1949.0,
  2.0,
  11.0,
  7.3,
  0.04382513661202184,
  0.0773224043715847,
  0.12295081967213115],
 'time_7': [36.3,
  96.9,
  983.0,
  1949.0,
  2.0,
  11.0,
  7.3,
  0.06098245614035089,
  0.33508771929824

# Form a dataframe where each row is an individual bridge time series, identified by it's bridge id

In [29]:
final_df = pd.DataFrame(columns=['Bridge_id', 'time_0', 'time_1', 'time_2', 'time_3', 'time_4', 'time_5', 'time_6', 'time_7',
                                'time_8', 'time_9', 'time_10', 'time_11', 'time_12', 'time_13', 'time_14', 'time_15', 'time_16',
                                'time_17', 'time_18', 'time_19', 'time_20', 'time_21'])

for temp_dict in list_of_dicts:
    final_df = final_df.append(temp_dict, ignore_index=True)

# View this dataframe

In [30]:
final_df

Bridge_id                                             time_0  \
0    CALHAN-8TH ST.   [36.0, 97.0, 428.0, 1949.0, 2.0, 10.9, 7.3, 0....   
1    CSG-C.80-07.65   [36.0, 83.9, 417.0, 1970.0, 2.0, 6.6, 6.4, 0.0...   
2    CSG-D.04-10.42   [36.0, 82.0, 1836.0, 1955.0, 2.0, 7.6, 4.0, 0....   
3    CSG-D.37-15.67   [36.0, 97.0, 87.0, 1984.0, 2.0, 12.8, 3.0, 0.0...   
4    CSG-D.90-10.15   [67.5, 80.1, 16737.0, 1960.0, 12.0, 18.5, 7.6,...   
..               ...                                                ...   
517  I-17-EP          [87.3, 82.0, 78200.0, 1959.0, 0.0, 11.8, 16.2,...   
518  I-17-G           [87.3, 82.0, 13500.0, 1942.0, 0.0, 10.9, 14.0,...   
519  I-17-HK          [87.3, 82.0, 38400.0, 1972.0, 0.0, 22.5, 35.1,...   
520  I-17-JH          [87.3, 82.0, 10500.0, 1995.0, 0.0, 12.9, 20.7,...   
521  J-18-BK          [87.3, 82.0, 21800.0, 1976.0, 0.0, 11.5, 28.0,...   

                                                time_1  \
0    [36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3, 0....   
1    [36.0, 70.9, 351.0, 1970.0, 2.0, 6.6, 3.0, 0.0...   
2    [36.0, 84.3, 1459.0, 1955.0, 2.0, 7.7, 4.0, 0....   
3    [36.0, 97.0, 305.0, 1984.0, 2.0, 12.8, 3.0, 0....   
4    [36.0, 80.5, 13460.0, 1960.0, 12.0, 18.5, 7.6,...   
..                                                 ...   
517  [87.3, 82.0, 93800.0, 1959.0, 0.0, 11.8, 16.2,...   
518     [87.3, 82.0, 13500.0, 1942.0, 0.0, 10.9, 14.0]   
519  [87.3, 82.0, 38000.0, 1972.0, 0.0, 22.5, 35.1,...   
520  [87.3, 82.0, 32904.0, 1995.0, 0.0, 12.9, 20.7,...   
521  [87.3, 82.0, 25600.0, 1976.0, 0.0, 11.5, 28.0,...   

                                                time_2  \
0    [36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3, 0....   
1    [36.0, 70.9, 351.0, 1970.0, 2.0, 6.6, 3.0, 0.0...   
2    [36.0, 84.3, 1459.0, 1955.0, 2.0, 7.7, 4.0, 0....   
3    [36.0, 97.0, 305.0, 1984.0, 2.0, 12.8, 3.0, 0....   
4    [36.0, 80.5, 13460.0, 1960.0, 12.0, 18.5, 7.6,...   
..                                                 ...   
517     [87.3, 82.0, 93800.0, 1959.0, 0.0, 11.8, 16.2]   
518     [87.3, 82.0, 13500.0, 1942.0, 0.0, 10.9, 14.0]   
519     [87.3, 82.0, 38000.0, 1972.0, 0.0, 22.5, 35.1]   
520  [87.3, 82.0, 32904.0, 1995.0, 0.0, 12.9, 20.7,...   
521  [87.3, 82.0, 25600.0, 1976.0, 0.0, 11.5, 28.0,...   

                                             time_3  \
0       [36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3]   
1        [36.0, 70.9, 351.0, 1970.0, 2.0, 6.6, 3.0]   
2       [36.0, 84.3, 1459.0, 1955.0, 2.0, 7.7, 4.0]   
3       [36.0, 97.0, 305.0, 1984.0, 2.0, 12.8, 3.0]   
4    [36.0, 80.5, 13460.0, 1960.0, 12.0, 18.5, 7.6]   
..                                              ...   
517  [87.3, 82.0, 93800.0, 1959.0, 0.0, 11.8, 16.2]   
518  [87.3, 82.0, 13500.0, 1942.0, 0.0, 10.9, 14.0]   
519  [87.3, 82.0, 38000.0, 1972.0, 0.0, 22.5, 35.1]   
520  [87.3, 82.0, 32904.0, 1995.0, 0.0, 12.9, 20.7]   
521  [87.3, 82.0, 25600.0, 1976.0, 0.0, 11.5, 28.0]   

                                                time_4  \
0    [36.0, 96.9, 955.0, 1949.0, 2.0, 10.9, 7.3, 0....   
1    [36.0, 70.9, 351.0, 1970.0, 2.0, 6.6, 3.0, 0.0...   
2    [36.0, 84.3, 1459.0, 1955.0, 2.0, 7.7, 3.4, 0....   
3    [36.0, 97.0, 305.0, 1984.0, 2.0, 12.8, 3.0, 0....   
4    [36.0, 80.5, 13460.0, 1960.0, 12.0, 18.5, 7.6,...   
..                                                 ...   
517     [87.3, 82.0, 93800.0, 1959.0, 0.0, 11.8, 16.2]   
518     [87.3, 82.0, 13500.0, 1942.0, 0.0, 10.9, 14.0]   
519     [87.3, 82.0, 38000.0, 1972.0, 0.0, 22.5, 35.1]   
520  [87.3, 82.0, 36024.0, 1995.0, 0.0, 12.1, 20.7,...   
521  [87.3, 82.0, 21055.0, 1976.0, 0.0, 11.5, 28.0,...   

                                                time_5  \
0    [36.3, 97.0, 955.0, 1949.0, 2.0, 11.0, 7.0, 0....   
1    [36.3, 76.0, 351.0, 1970.0, 2.0, 6.6, 3.0, 0.0...   
2    [36.3, 83.4, 1459.0, 1955.0, 2.0, 7.7, 3.0, 0....   
3    [36.3, 97.0, 305.0, 1984.0, 2.0, 12.8, 3.0, 0....   
4    [36.3, 81.2, 13460.0, 1960.0, 12.0, 18.6, 7.6,...   
..        

# Write the dataframe to a .csv and exclude indices

In [31]:
final_df.to_csv('Time_Series_For_Clustering_El_Paso_with_Weather_data.csv', index=False)